In [1]:
import numpy as np
import matplotlib
import os
import pandas as pd
#matplotlib.use('PDF')
from matplotlib import pyplot as plt
from tigramite import plotting as tp
import scipy
import sklearn
from sklearn.cluster import KMeans, MeanShift, DBSCAN
from sklearn.preprocessing import scale

import numpy.ma as ma
from netCDF4 import Dataset as NetCDFFile
import os


#import geopandas as gpd
#import geoplot as gplt

from sklearn.decomposition import PCA, TruncatedSVD

import sklearn.decomposition

import sklearn.manifold.t_sne as tsne

import xarray as xr


In [2]:
step=91
extent="intra" #"intra") #inter or intra # irrelevant for MovingWindow
tau_min=0
tau_max=5
min_len=5
Dataset='Jake'
attribute2='_RgNotDriver'
attribute='_'
var_names = ["Rg","T","NEE","VPD","H","LE"]
event_mask_use=['None']
savepath="/home/christopher/BGI/scratch/ckrich/Projects/EcosystemCharacterisationByCausalNetworks"
method='parcor'
processing='_anomalysmooth' 
mask_type='y'
quality_value=0.9
pc_alpha='None'
minlength=5 #minimal timeseries length in years
alpha_level=1


In [6]:
    nv=len(var_names)


In [4]:
towers

['US-Prr.DD.2010.2014.nc',
 'US-KS1.DD.2002.2002.nc',
 'PA-SPs.DD.2007.2009.nc',
 'US-Blo.DD.1997.2007.nc',
 'US-Fmf.DD.2005.2006.nc',
 'UK-Tad.DD.2001.2001.nc',
 'ES-ES1.DD.1999.2006.nc',
 'RU-Fyo.DD.1998.2014.nc',
 'US-SRM.DD.2004.2014.nc',
 'CN-Din.DD.2003.2005.nc',
 'DE-RuR.DD.2011.2014.nc',
 'SE-St1.DD.2012.2014.nc',
 'AR-Vir.DD.2009.2012.nc',
 'IT-Cpz.DD.1997.2009.nc',
 'US-SP1.DD.2000.2005.nc',
 'DK-Sor.DD.1996.2014.nc',
 'DE-Lnf.DD.2002.2012.nc',
 'US-Bo2.DD.2004.2006.nc',
 'CA-TP3.DD.2002.2014.nc',
 'DK-Fou.DD.2005.2005.nc',
 'US-ORv.DD.2011.2011.nc',
 'CA-SJ3.DD.2004.2005.nc',
 'US-Sta.DD.2005.2009.nc',
 'DE-Akm.DD.2009.2014.nc',
 'US-Aud.DD.2002.2006.nc',
 'CA-Oas.DD.1996.2010.nc',
 'US-FPe.DD.2000.2006.nc',
 'BR-Ji2.DD.2000.2002.nc',
 'PA-SPn.DD.2007.2009.nc',
 'AU-Lox.DD.2008.2009.nc',
 'CH-Fru.DD.2005.2014.nc',
 'IT-Tor.DD.2008.2014.nc',
 'AU-Wom.DD.2010.2014.nc',
 'US-Me6.DD.2010.2014.nc',
 'GH-Ank.DD.2011.2014.nc',
 'CA-TPD.DD.2012.2014.nc',
 'BE-Jal.DD.2006.2006.nc',
 

In [9]:
towers=os.listdir( "%s/Outputs/%s/%s" % (savepath,Dataset,var_names))

#towers=['DE-Hai.DD.2000.2012.nc']#,'DE-Tha.DD.1996.2014.nc','DE-Lnf.DD.2002.2012.nc', 'DE-Obe.DD.2008.2014.nc','DE-Spw.DD.2010.2014.nc']#,'AU-Dry.DD.2008.2014.nc','CZ-BK2.DD.2004.2012.nc',
 #'IT-Ro1.DD.2000.2008.nc',
 #'CA-NS5.DD.2001.2005.nc',
 #'US-UMd.DD.2007.2014.nc',
 #'DE-Kli.DD.2004.2014.nc',
 #'RU-Cok.DD.2003.2014.nc',
 #'ES-Amo.DD.2007.2012.nc',]

#towers=['DE-Hai.DD.2000.2012.nc', 'US-Ton.DD.2001.2014.nc', 'FR-Pue.DD.2000.2014.nc','DE-Tha.DD.1996.2014.nc','AU-DaP.DD.2007.2013.nc', 'DK-ZaH.DD.2000.2014.nc',
 #      'RU-Fyo.DD.1998.2014.nc','NL-Hor.DD.2004.2011.nc', 'DE-Geb.DD.2001.2014.nc',  'BE-Vie.DD.1996.2014.nc',
  #      ]

W=len(var_names)
    
if step==91:
    season_mask_use=['Jan', 'Feb', 'Mar', 'Apr', 'Maj', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec'] # ["winter", "spring","summer","autumn"] #["summer"] #["winter", "spring","summer","autumn"] #
elif step==365:
    season_mask_use=['']
    month_mask_use=['']

metadata_dict={}

time_series_dict={}
netcdf_var_dict={"Rg":"SW_IN_F", "T":"TA_F", "NEE":"NEE_VUT_USTAR50", "VPD":"VPD_F", "H":"H_CORR", "LE":"LE_CORR", 'P':'P_F'}
netcdf_SWC_dict={"SWC1":'SWC_F_MDS_1',"SWC2":'SWC_F_MDS_2',"SWC3":'SWC_F_MDS_3',"SWC4":'SWC_F_MDS_4',"SWC5":'SWC_F_MDS_5',"SWC6":'SWC_F_MDS_6'}
netcdf_SWCq_dict={"SWC1":'SWC_F_MDS_1_QC',"SWC2":'SWC_F_MDS_2_QC',"SWC3":'SWC_F_MDS_3_QC',"SWC4":'SWC_F_MDS_4_QC',"SWC5":'SWC_F_MDS_5_QC',"SWC6":'SWC_F_MDS_6_QC'}

df_val=pd.DataFrame()
df_p=pd.DataFrame()
df_q=pd.DataFrame()

for t,fluxtower in enumerate(towers): 
    print(fluxtower)
  #  if not fluxtower[0:6]=='DE-Hai':
   #     continue
    startyear=eval(fluxtower[-12:-8])
    endyear=eval(fluxtower[-7:-3])
    ys=np.arange(startyear,endyear+1,1)
    
    if Dataset=='long':
        path="/home/christopher/BGI/data/DataStructureMDI/DATA/Incoming/Fluxnet/berkeley_012016/Data/DD/2016_11"
    elif Dataset=='Jake':
        fluxtower=fluxtower[0:6]
        path='/home/christopher/BGI/work_2/fluxnet-BGI/data/%s/eddy_covariance/L1_daily' % fluxtower[0:6]
        
        
    if Dataset=="long":
        filename='%s%s' % (fluxtower, attribute)
#        path="/Net/Groups/BGI/data/DataStructureMDI/DATA/Incoming/Fluxnet/berkeley_012016/Data/DD/2016_11"
        path="/home/christopher/BGI/data/DataStructureMDI/DATA/Incoming/Fluxnet/berkeley_012016/Data/DD/2016_11"
        if os.path.isfile('%s/%s' %  (path, towers[t])) == False:
            print('not found: %s/%s' %  (path, towers[t]))
            continue
        print("found",fluxtower)
        ts=NetCDFFile('%s/%s' % (path,towers[t]))
        L=len(ts.dimensions["time"])
        if L/minlength<365:
            print("TS too short")
            continue
        netcdf_var_dict={"Rg": "SW_IN_F", "T": "TA_F", "VPD": "VPD_F", "NEE": "NEE_VUT_USTAR50", "LE": "LE_CORR", "H": "H_CORR", 'P':'P_F','GPP':'GPP_NT_CUT_MEAN' }
        netcdf_SWC_dict={"SWC1":'SWC_F_MDS_1',"SWC2":'SWC_F_MDS_2',"SWC3":'SWC_F_MDS_3',"SWC4":'SWC_F_MDS_4',"SWC5":'SWC_F_MDS_5',"SWC6":'SWC_F_MDS_6'}
        netcdf_SWCq_dict={"SWC1":'SWC_F_MDS_1_QC',"SWC2":'SWC_F_MDS_2_QC',"SWC3":'SWC_F_MDS_3_QC',"SWC4":'SWC_F_MDS_4_QC',"SWC5":'SWC_F_MDS_5_QC',"SWC6":'SWC_F_MDS_6_QC'}
        var_names_QC_dict={"Rg": "SW_IN_F", "T": "TA_F", "VPD": "VPD_F", "NEE": "NEE_VUT_USTAR50", "LE": "LE_F_MDS", "H": "H_F_MDS" }
        availableSWC=["SWC1","SWC2","SWC3","SWC4","SWC5","SWC6"]
        
        #read time series
        for var in var_names+['P','GPP']:
            time_series_dict[var]=np.squeeze(ts.variables[netcdf_var_dict[var]][:])
        if ma.is_masked(time_series_dict["H"].sum()):
            time_series_dict['H']=np.squeeze(ts.variables['H_F_MDS'][:])
            time_series_dict['LE']=np.squeeze(ts.variables['LE_F_MDS'][:])

        Data_dict={}
        Data_q_dict={}
        for var in var_names:
            Data_dict[var]=np.squeeze(ts.variables[netcdf_var_dict[var]][:])
            Data_q_dict[var]=np.squeeze(ts.variables[var_names_QC_dict[var]+'_QC'][:])

        month=np.squeeze(ts.variables["month"])#
        day=np.squeeze(ts.variables["day"])#;
        year=np.squeeze(ts.variables["year"])#[:]

      #  Data=np.array(list(Data_dict.values())).T
       # Data_q=np.array(list(Data_q_dict.values())).T
        #Data[np.isnan(Data)]=-9999
        print("finishedreadingData")
    elif Dataset=='short':
        filename='%s%s' % (fluxtower, attribute)
        path="'/home/christopher/BGI/data/DataStructureMDI/DATA/site/Fluxnet/daily/level5_new_v2_newRpot_DayNight/Data_AUG2018/"
        if os.path.isfile('%s/%s' %  (path, towers[t])) == False:
            print('not found: %s/%s' %  (path, towers[t]))
            continue
        print("found",fluxtower)
        ts=NetCDFFile('%s/%s' % (path,fluxtower))

        
        var_names = ["Rg","T","NEE_N","NEE_D","VPD","H","LE"]
        Dataset='short'


        Data_dict={}
        Data_q_dict={}

        Data_dict['Rg']=ts['Rg_f'][:].data
        Data_dict['T']=ts['Tair_f'][:].data
        Data_dict['NEE_N']=ts['NEE_f_Night_m2'][:].data
        Data_dict['NEE_D']=ts['NEE_f_Day_m2'][:].data
        Data_dict['VPD']=ts['VPD_f'][:].data
        Data_dict['H']=ts['H_f'][:].data
        Data_dict['LE']=ts['LE_f'][:].data

        Data_q_dict['Rg']=ts['Rg_fqcOK'][:].data
        Data_q_dict['T']=ts['Tair_fqcOK'][:].data
        Data_q_dict['NEE_N']=ts['NEE_f_Night_percent_fqc_m2'][:].data
        Data_q_dict['NEE_D']=ts['NEE_f_Day_percent_fqc_m2'][:].data
        Data_q_dict['VPD']=ts['VPD_fqcOK'][:].data
        Data_q_dict['H']=ts['H_fqcOK'][:].data
        Data_q_dict['LE']=ts['LE_fqcOK'][:].data

        month=np.squeeze(ts.variables["month"])#
        day=np.squeeze(ts.variables["day"])#;
        year=np.squeeze(ts.variables["year"])#[:]
        Rg_pot=np.squeeze(ts.variables["Rg_pot"])

        Data=np.array(list(Data_dict.values())).T
        Data_q=np.array(list(Data_q_dict.values())).T
        Data[np.isnan(Data)]=-9999
        #set data to missing value if quality flag = 0 (might be hard, but needed to kick out Hainich last years)
        Data[Data_q==0]=-9999
        Data=np.ma.array(Data, mask=Data==-9999)

        W=len(var_names)
        L=len(Data_dict[var_names[0]])
    elif Dataset=='Jake':
        print(fluxtower)
        fluxtower=fluxtower[0:6]
        filename='%s%s' % (fluxtower, attribute)
        path='/home/christopher/BGI/work_2/fluxnet-BGI/data/%s/eddy_covariance/L1_daily/' % fluxtower
#        path='/Net/Groups/BGI/work_2/fluxnet-BGI/data/%s/eddy_covariance/L1_daily/' % fluxtower
        ts = xr.open_mfdataset(path +fluxtower+'.DD.*.nc')
        L=ts.dims["time"]
        if L/minlength<365:
            print("TS too short")
            continue        
        netcdf_var_dict={"Rg": "SW_IN", "T": "TA", "VPD": "VPD", "NEE": "NEE", "LE": "LE", "H": "H", "P":"P",'GPP':'GPP_NT' }
        netcdf_SWC_dict={"SWC1":'SWC_1',"SWC2":'SWC_2'}
        netcdf_SWCq_dict={"SWC1":'SWC_1_QC',"SWC2":'SWC_2_QC'}
        availableSWC=["SWC1","SWC2"]
        
        #read time series
        for var in var_names+['P','GPP']:
            time_series_dict[var]=np.squeeze(ts.variables[netcdf_var_dict[var]][:]).values

        time=pd.DatetimeIndex(np.squeeze(ts.variables["time"][:]).values)
        day=time.day
        month=time.month
        year=time.year

        minyear=year.min()
        maxyear=year.max()

        fluxtower=fluxtower+'.DD.%s.%s.nc'%(minyear,maxyear)
     #   metadata_dict['IGBP']=ts.attrs['IGBP_class']
      #  metadata_dict['Elevation']=ts.attrs['Elevation']
       # metadata_dict['Climate_class']=ts.attrs['Climate_class']
        #metadata_dict['Climate_Group']=ts.attrs['Climate_Group']

        print(fluxtower)

       # Data=np.array(list(Data_dict.values())).T
       # Data_q=np.array(list(Data_q_dict.values())).T
       # Data[np.isnan(Data)]=-9999    

    
    print(fluxtower)

    
    if extent=="intra":
        year_mask_use = [y for (i,y) in enumerate(ys)]
    elif extent=="inter":
        year_mask_use = ["%s-%s"%(min(ys),max(ys))]
   
    # loading data and creating mask for calculating cumulative precip from that season and year in this tower
#    if os.path.isfile('%s/%s' %  (path, fluxtower)) == False:
 #       print('not found: %s/%s' %  (path, fluxtower))
  #      continue
        
#    ts=NetCDFFile('%s/%s' % (path,fluxtower))


    # calc mean var value of site
    for var in var_names+['P','GPP']:
        metadata_dict[var+'_mean_y']=np.nanmean(time_series_dict[var])
        if ma.is_masked(metadata_dict[var+'_mean_y']):
            metadata_dict[var+'_mean_y']=np.nan

    metadata_dict['Tower']=fluxtower
    metadata_dict['lon']=np.squeeze(ts.variables["longitude"]).item()
    metadata_dict['lat']=np.squeeze(ts.variables["latitude"]).item()
    
#    month=np.squeeze(ts.variables["month"])#
 #   #day=np.squeeze(ts.variables["day"])#;
  #  year=np.squeeze(ts.variables["year"])#[:];

    #load soil moister data incl. qualityflag
    for SWC in availableSWC:
        time_series_dict[SWC]=np.squeeze(ts.variables[netcdf_SWC_dict[SWC]][:])
        time_series_dict[SWC+'q']=np.squeeze(ts.variables[netcdf_SWCq_dict[SWC]][:])
        
        
    # create 3 month monthly moving window mask
    month_mask_prel = np.ones((L,12))
    month_ind=[1,2,3,4,5,6,7,8,9,10,11,12,1]
    for m in month_ind[:-1]:
        for i in range(0, L):
            if month[i]==month_ind[m-2] or month[i]==month_ind[m-1] or month[i]==month_ind[m]:
                month_mask_prel[i,m-1]=False

    month_mask={}
    for i,mon in enumerate(['Jan', 'Feb', 'Mar', 'Apr', 'Maj', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']):
        month_mask[mon]=month_mask_prel[:,i]
   # month_mask['']=np.zeros((L,W))
        
    #Create season dataframe
    season_mask_prel = np.ones((L,4))
    for i in range(0, L):
        if month[i]==12 or month[i]==1 or month[i]==2:
            season_mask_prel[i,0]=False
        elif month[i]==3 or month[i]==4 or month[i]==5:
            season_mask_prel[i,1]=False
        elif month[i]==6 or month[i]==7 or month[i]==8:
            season_mask_prel[i,2]=False
        elif month[i]==9 or month[i]==10 or month[i]==11:
            season_mask_prel[i,3]=False

    season_mask={'': np.zeros((L)), 'winter':season_mask_prel[:,0], 'spring':season_mask_prel[:,1], 'summer':season_mask_prel[:,2], 'autumn':season_mask_prel[:,3],**month_mask}

    ##### Yearly mask

    ys=np.unique(year).astype(int)
    year_mask={y: ((year==y)==0) for (i,y) in enumerate(ys)} # add all years to mask
    year_mask["%s-%s"%(min(ys),max(ys))]=np.zeros((L)) #add zero mask

    for (i,s) in enumerate(season_mask_use):
      #  print('ys loop %s' % y)
        print(s)
        # calc mean var value of site per season
        data_mask=((season_mask[s]==0)==0)
        for var in var_names+['P','GPP']:
            metadata_dict[var+'_mean_s']=np.nanmean(ma.masked_array(time_series_dict[var], mask=data_mask))
            if ma.is_masked(metadata_dict[var+'_mean_s']):
                metadata_dict[var+'_mean_s']=np.nan
                
        for (j,y) in enumerate(year_mask_use):
            print('year %s' % y)
            for (l,e) in enumerate(event_mask_use):
                try:
                    path='%s/Outputs/%s/%s/%s/Data/%s/%s/01_Results_%s%s_%s_%s_%s_%s_%s_%s_%s_%s_%s%s.npy' % (savepath,Dataset,var_names, fluxtower, method, step, filename, processing, mask_type,quality_value, y,s, e,method, pc_alpha, tau_min, tau_max, attribute2)
                    result=np.load(path,allow_pickle=True).item()
                    print('found',s,y)
                except:
                    print("Did not find %s"%path)
                    continue
                vals=pd.DataFrame(result["val_matrix"].reshape((nv*nv*(tau_max-tau_min+1)))[np.newaxis,:])
                ps=pd.DataFrame(result["p_matrix"].reshape((nv*nv*(tau_max-tau_min+1)))[np.newaxis,:])
                qs=pd.DataFrame(result["q_matrix"].reshape((nv*nv*(tau_max-tau_min+1)))[np.newaxis,:])
                #labels[vertical_ind]=fluxtower

                data_mask=((np.roll(year_mask[y]==0,-31))*(season_mask[s]==0)==0)
                    
                for var in var_names+['P','GPP']:
                    metadata_dict[var+"_mean"]=np.nanmean(ma.masked_array(time_series_dict[var], mask=data_mask))
                    metadata_dict[var+"_max"]=np.nanmax(ma.masked_array(time_series_dict[var], mask=data_mask))
                    metadata_dict[var+"_min"]=np.nanmin(ma.masked_array(time_series_dict[var], mask=data_mask))
                    if ma.is_masked(metadata_dict[var+'_mean']):
                        metadata_dict[var+'_mean']=np.nan
                    if ma.is_masked(metadata_dict[var+'_max']):
                        metadata_dict[var+'_max']=np.nan
                    if ma.is_masked(metadata_dict[var+'_min']):
                        metadata_dict[var+'_min']=np.nan
             
                for i in availableSWC:
                    metadata_dict['%s_mean'%i]=np.nanmean(ma.masked_array(time_series_dict[i], mask=data_mask)).astype('f8')
                    metadata_dict['%sq_mean'%i]=np.nanmean(ma.masked_array(time_series_dict[i+'q'], mask=data_mask)).astype('f8')
                    if ma.is_masked(metadata_dict['%s_mean'%i]):
                        metadata_dict['%s_mean'%i]=np.nan
                    if ma.is_masked(metadata_dict['%sq_mean'%i]):
                        metadata_dict['%sq_mean'%i]=np.nan
                
           
                metadata_dict['Year']=y
                metadata_dict['Season']=s
                metadata_df=pd.DataFrame(metadata_dict,index=[0])
           
                df_val=df_val.append(pd.concat([metadata_df,vals], axis=1,sort=False),ignore_index=True,sort=False)
                df_p=df_p.append(pd.concat([metadata_df,ps],axis=1,sort=False),ignore_index=True,sort=False)
                df_q=df_q.append(pd.concat([metadata_df,qs],axis=1,sort=False),ignore_index=True,sort=False)

                results_df={"df_p":df_p,"df_q":df_q,"df_val":df_val}


                

US-Prr.DD.2010.2014.nc
US-Prr
US-Prr.DD.2010.2014.nc
US-Prr.DD.2010.2014.nc
Jan
year 2010
Did not find /home/christopher/BGI/scratch/ckrich/Projects/EcosystemCharacterisationByCausalNetworks/Outputs/Jake/['Rg', 'T', 'NEE', 'VPD', 'H', 'LE']/US-Prr.DD.2010.2014.nc/Data/parcor/91/01_Results_US-Prr__anomalysmooth_y_0.9_2010_Jan_None_parcor_None_0_5_RgNotDriver.npy
year 2011
found Jan 2011


/home/christopher/anaconda3/envs/tigraClustOldPandas/lib/python3.7/site-packages/ipykernel_launcher.py:285: RuntimeWarning: Mean of empty slice


year 2012
Did not find /home/christopher/BGI/scratch/ckrich/Projects/EcosystemCharacterisationByCausalNetworks/Outputs/Jake/['Rg', 'T', 'NEE', 'VPD', 'H', 'LE']/US-Prr.DD.2010.2014.nc/Data/parcor/91/01_Results_US-Prr__anomalysmooth_y_0.9_2012_Jan_None_parcor_None_0_5_RgNotDriver.npy
year 2013
found Jan 2013
year 2014


/home/christopher/anaconda3/envs/tigraClustOldPandas/lib/python3.7/site-packages/ipykernel_launcher.py:285: RuntimeWarning: Mean of empty slice


found Jan 2014
Feb
year 2010
Did not find /home/christopher/BGI/scratch/ckrich/Projects/EcosystemCharacterisationByCausalNetworks/Outputs/Jake/['Rg', 'T', 'NEE', 'VPD', 'H', 'LE']/US-Prr.DD.2010.2014.nc/Data/parcor/91/01_Results_US-Prr__anomalysmooth_y_0.9_2010_Feb_None_parcor_None_0_5_RgNotDriver.npy
year 2011
Did not find /home/christopher/BGI/scratch/ckrich/Projects/EcosystemCharacterisationByCausalNetworks/Outputs/Jake/['Rg', 'T', 'NEE', 'VPD', 'H', 'LE']/US-Prr.DD.2010.2014.nc/Data/parcor/91/01_Results_US-Prr__anomalysmooth_y_0.9_2011_Feb_None_parcor_None_0_5_RgNotDriver.npy
year 2012


...

found Dec 2003
year 2004


/home/christopher/anaconda3/envs/tigraClustOldPandas/lib/python3.7/site-packages/ipykernel_launcher.py:285: RuntimeWarning: Mean of empty slice
/home/christopher/anaconda3/envs/tigraClustOldPandas/lib/python3.7/site-packages/ipykernel_launcher.py:285: RuntimeWarning: Mean of empty slice


found Dec 2004
year 2005


/home/christopher/anaconda3/envs/tigraClustOldPandas/lib/python3.7/site-packages/ipykernel_launcher.py:285: RuntimeWarning: Mean of empty slice
/home/christopher/anaconda3/envs/tigraClustOldPandas/lib/python3.7/site-packages/ipykernel_launcher.py:285: RuntimeWarning: Mean of empty slice


Did not find /home/christopher/BGI/scratch/ckrich/Projects/EcosystemCharacterisationByCausalNetworks/Outputs/Jake/['Rg', 'T', 'NEE', 'VPD', 'H', 'LE']/CA-Ojp.DD.1999.2005.nc/Data/parcor/91/01_Results_CA-Ojp__anomalysmooth_y_0.9_2005_Dec_None_parcor_None_0_5_RgNotDriver.npy
FI-Sii.DD.2004.2005.nc
FI-Sii
TS too short
IT-Vig.DD.2004.2005.nc
IT-Vig
TS too short
RU-Ha1.DD.2002.2004.nc
RU-Ha1
TS too short
US-AR2.DD.2009.2012.nc
US-AR2
TS too short
US-Wi3.DD.2002.2004.nc
US-Wi3
TS too short


In [8]:
results_df

{'df_p':      Rg_mean_y   T_mean_y  NEE_mean_y  VPD_mean_y   H_mean_y  LE_mean_y  \
 0   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 1   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 2   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 3   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 4   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 5   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 6   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 7   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 8   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 9   104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 10  104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 11  104.690727  -3.381252   -0.201845    3.120052  14.422005  13.211999   
 12 

In [11]:
berkeley=pd.read_csv('../Data/FLUXNET2015_data-availability-20181214151739.csv',index_col=0)

lathuile=pd.read_csv('../Data/LaThuile_SynthDataSummary.csv',skiprows=1,index_col=0)

In [12]:
for typ in results_df.keys():
    for i in results_df[typ].index:
        tower,year = results_df[typ].loc[i,['Tower','Year']].values

        if (str(int(year)) in berkeley.columns) and (tower[0:6] in berkeley.index):
          #  print(tower[0:6],str(int(year)), 'in Berkley')
            results_df[typ].loc[i,'DataPolicy']=berkeley.loc[tower[0:6],str(int(year))]
        elif (str(int(year)) in lathuile.columns) and (tower[0:6] in lathuile.index):
          #  print(tower[0:6],str(int(year)), 'in LaThuile')
            results_df[typ].loc[i,'DataPolicy']=lathuile.loc[tower[0:6],str(int(year))]
        else:
            print(tower[0:6],str(int(year)), 'not found')


In [13]:
np.save("../Data/df_results_t_y_m_%s_%s_%s_%s_nanmean_DataPolicy.npy" % (Dataset,extent,step,tau_max),results_df)

In [2]:
results_df[typ]

NameError: name 'results_df' is not defined

In [14]:
def prepdata(Dataset,extent,step,var_names,tau_max,tau_min,alpha_level,min_len=None,matrixtype='df_val_q'):
    nv=len(var_names)
    results_df=np.load("../Data/df_results_t_y_m_%s_%s_%s_%s_nanmean_DataPolicy.npy" % (Dataset,extent,step,tau_max), allow_pickle=True).item()
    df_p  =results_df["df_p"]
    df_q  =results_df["df_q"]
    df_val=results_df["df_val"]


    link_q=df_q.copy()
    link_q[np.arange(0,nv*nv*(tau_max-tau_min+1))]=df_q[np.arange(0,nv*nv*(tau_max-tau_min+1))]<alpha_level
    link_p=df_p.copy()
    link_p[np.arange(0,nv*nv*(tau_max-tau_min+1))]=df_p[np.arange(0,nv*nv*(tau_max-tau_min+1))]<alpha_level


    df_val_q=df_val.copy()
    df_val_q[np.arange(0,nv*nv*(tau_max-tau_min+1))]=df_val_q[np.arange(0,nv*nv*(tau_max-tau_min+1))]*(link_q[np.arange(0,nv*nv*(tau_max-tau_min+1))])
    df_val_p=df_val.copy()
    df_val_p[np.arange(0,nv*nv*(tau_max-tau_min+1))]=df_val_p[np.arange(0,nv*nv*(tau_max-tau_min+1))]*(link_p[np.arange(0,nv*nv*(tau_max-tau_min+1))])

    data=eval(matrixtype).copy()

    #data=link_q
    #data=df_val
    data=data.iloc[data[np.arange(0,nv*nv*(tau_max-tau_min+1))].dropna().index]
    
#    data['num_years']=0
    for t in data['Tower'].unique():
        ind=data[data['Tower']==t].index
#        ny=int(t[12:16])-int(t[7:11])+1
        ny=int(t[15:19])-int(t[10:14])+1
        data.loc[ind,'num_years']=ny
        
    if min_len != None:
        data=data[data['num_years']>=min_len]
    #select season
    #data=data[data["Season"]=="summer"]
    #data=pd.concat([data[(data["Lat"]>0)&(data["Season"]=="summer")],data[(data["Lat"]<0)&(data["Season"]=="winter")]])
    #select towers by coordinate
    #data=data[(data["Lat"]>35)&(data["Lat"]<85)&(data["Lon"]<60)&(data["Lon"]>-15)]

    #data=data[data["Season"]=="summer"]

    # add vegetation type to data
    vegtype=pd.read_csv("../Data/FluxtowerVegetationType.csv")[["SITE_ID","IGBP"]]
    data["IGBP"]=""
    for fluxtower in data["Tower"].unique():
        indices=data[data["Tower"]==fluxtower].index
        try:
            data.loc[indices,"IGBP"]=vegtype[vegtype["SITE_ID"]==fluxtower[:6]]["IGBP"].values[0]
        #data["IGBP"][(data["IGBP"]==fluxtower[:6])]=
        except:
            path='/home/christopher/BGI/work_2/fluxnet-BGI/data/%s/eddy_covariance/L1_daily/' % fluxtower[0:6]
            ts = xr.open_mfdataset(path +fluxtower[0:6]+'.DD.*.nc')
            siteid=ts.attrs['Site_ID']
            igbp=ts.attrs['IGBP_class']
            vegtype=vegtype.append({"SITE_ID":siteid,"IGBP":igbp},ignore_index=True)

    vegtype.to_csv("../Data/FluxtowerVegetationType.csv")
    
    data["Vegetation"]=data["IGBP"].copy()
    data["Vegetation"]=data["Vegetation"].replace("ENF","Fo").replace("DBF","Fo").replace("EBF","Fo").replace("MF","Fo")
    data["Vegetation"]=data["Vegetation"].replace("GRA","Gl")
    data["Vegetation"]=data["Vegetation"].replace("CRO","Cl").replace("CVM","Cl")
    data["Vegetation"]=data["Vegetation"].replace("WET","Wl")
    data["Vegetation"]=data["Vegetation"].replace("OSH","Sl").replace("CSH","Sl")
    data["Vegetation"]=data["Vegetation"].replace("SAV","Sa").replace("WSA","Sa")



    # create labels and add network summed over lags to data
    labels_cont=[]
    labels_lag=[]

    matrix=np.zeros((nv,nv,tau_max-tau_min+1),'U8')
    for i,d in enumerate(var_names):
        for j,r in enumerate(var_names):
            #for t in [0,1,2,3,4,5]:
            #labels.append(d + "→" +r+':1-6')
            labels_cont.append(d + "→" +r+':0')
            labels_lag.append(d + "→" +r+':1-%s'%(tau_max))
               # matrix[i,j,t]=d + "→" +r+str(t)

    for l,i in enumerate(np.arange(0,nv*nv*(tau_max-tau_min+1),tau_max+1-tau_min)):
        data[labels_cont[l]]=data[i]
        data[labels_lag[l]]=data[np.arange(i+1,i+tau_max+1)].sum(axis=1)

    # set columns to categrical dtype
   # data["Season"]=data["Season"].astype(pd.api.types.CategoricalDtype(categories=["winter", "spring", "summer", "autumn"],ordered=True))
    data["Season"]=data["Season"].astype(pd.api.types.CategoricalDtype(categories=['Jan', 'Feb', 'Mar', 'Apr', 'Maj', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec'],ordered=True))
    data.sort_values(["Tower","Year","Season"],inplace=True)

    data["Season_num"]=""
    for i,s in enumerate(['Jan', 'Feb', 'Mar', 'Apr', 'Maj', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']):
        indices=data[data["Season"]==s].index
        data.loc[indices,"Season_num"]=i

    data["Tower_num"]=""
    for i,t in enumerate(data["Tower"].unique()):
        indices=data[data["Tower"]==t].index
        data.loc[indices,"Tower_num"]=i

    data["IGBP_num"]=""
    for i,t in enumerate(data["IGBP"].unique()):
        indices=data[data["IGBP"]==t].index
        data.loc[indices,"IGBP_num"]=i

    data["Vegetation_num"]=""
    for i,t in enumerate(data["Vegetation"].unique()):
        indices=data[data["Vegetation"]==t].index
        data.loc[indices,"Vegetation_num"]=i

    data["Country"]=""
    for i,t in enumerate(data["Tower"].unique()):
        indices=data[data["Tower"]==t].index
        data.loc[indices,"Country"]=t[0:2]
    
    ## find month with on average maximal GPP and add to dataframe
    GPPmax=data.groupby(['Tower','Season']).mean()[['GPP_mean']].groupby(['Tower']).idxmax()

    data['Month_GPPmax']=''
    for t in data.Tower.unique():
        indices=data[data.Tower==t].index.values
        data.loc[indices,('Month_GPPmax')]=GPPmax.loc[t,'GPP_mean'][1]

    data['PeakGrowingMonth']=''
    data['PeakGrowingMonth']=data['Season']==data['Month_GPPmax']

    data['PeakGrowingMonth_Year']=False
    for t in data.Tower.unique():
        for y in data[data.Tower==t]['Year'].unique():
            indices=data[(data.Tower==t) & (data.Year==y)].index.values
            if not data.loc[indices,'PeakGrowingMonth'].any():
                continue
            ind_maxGPP_year_tower=data.loc[indices,'GPP_mean'].idxmax()
            data.loc[ind_maxGPP_year_tower,('PeakGrowingMonth_Year')]=True
            
    # create Koepen Geiger columns
    KG_exp=pd.read_json('/home/christopher/BGI/work_2/fluxnet-BGI/site_metadata_collections/KoeppenGeigerDefs.json')
    KG_t=pd.read_json('/home/christopher/BGI/work_2/fluxnet-BGI/site_metadata_collections/siteKopppenGeiger.json', typ='series')

    data['KoeppenGeigerType']=np.nan
    data['KoeppenGeigerGroup']=np.nan
    data['KoeppenGeigerSpec']=''

    for t in data['Tower'].unique():
        index_t=data[data['Tower']==t].index
        groups_KG=KG_exp.keys()
        try:
            num_t=KG_t[t[0:6]]
        except:
            continue
        spec_t=groups_KG[KG_exp.loc[0,:]==num_t].values[0]
        group_t=KG_exp.loc[1,spec_t]
        data.loc[index_t,'KoeppenGeigerType']=int(num_t)
        data.loc[index_t,'KoeppenGeigerGroup']=int(group_t)
        data.loc[index_t,'KoeppenGeigerSpec']=spec_t

    # stand age
    stand_age=pd.read_csv('../Data/Mirco_Nature_SupMat.csv')

    data['StandAge']=np.nan

    for t in data['Tower'].unique():
        print(t)
        index_t=data[data['Tower']==t].index
        try:
            num_t=np.where(stand_age['site.code']==t[0:6])[0][0]
            data.loc[index_t,'StandAge']=stand_age.loc[num_t,'Age']

        except:
            continue
    data['Season']=pd.Categorical(data['Season'], ['Jan','Feb', 'Mar', 'Apr', 'Maj', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct','Nov', 'Dec'])
    data.reset_index(inplace=True,drop=True)
    return data

In [15]:
alpha_level=0.1

In [16]:
data=prepdata(Dataset,extent,step,var_names,tau_max,tau_min,alpha_level,matrixtype='df_val_q',min_len=min_len)

AT-Neu.DD.2002.2012.nc
AU-ASM.DD.2010.2014.nc
AU-Cpr.DD.2010.2014.nc
AU-DaP.DD.2007.2013.nc
AU-DaS.DD.2008.2014.nc
AU-Dry.DD.2008.2014.nc
AU-How.DD.2001.2014.nc
AU-Stp.DD.2008.2014.nc
AU-Tum.DD.2001.2014.nc
AU-Wom.DD.2010.2014.nc
BE-Bra.DD.1996.2014.nc
BE-Lon.DD.2004.2014.nc
BE-Vie.DD.1996.2014.nc
BR-Ma2.DD.1999.2006.nc
BR-Sa1.DD.2002.2011.nc
BR-Sa3.DD.2000.2004.nc
CA-Ca1.DD.1997.2005.nc
CA-Ca2.DD.2000.2005.nc
CA-Ca3.DD.2001.2005.nc
CA-Gro.DD.2003.2014.nc
CA-Let.DD.1998.2005.nc
CA-Mer.DD.1998.2005.nc
CA-NS1.DD.2001.2005.nc
CA-NS2.DD.2001.2005.nc
CA-NS3.DD.2001.2005.nc
CA-NS5.DD.2001.2005.nc
CA-NS6.DD.2001.2005.nc
CA-Oas.DD.1996.2010.nc
CA-Obs.DD.1997.2010.nc
CA-Ojp.DD.1999.2005.nc
CA-Qcu.DD.2001.2006.nc
CA-Qfo.DD.2003.2010.nc
CA-SF2.DD.2001.2005.nc
CA-SF3.DD.2001.2006.nc
CA-SJ1.DD.2001.2005.nc
CA-TP1.DD.2002.2014.nc
CA-TP2.DD.2002.2007.nc
CA-TP3.DD.2002.2014.nc
CA-TP4.DD.2002.2014.nc
CH-Cha.DD.2005.2014.nc
CH-Dav.DD.1997.2014.nc
CH-Fru.DD.2005.2014.nc
CH-Lae.DD.2004.2014.nc
CH-Oe1.DD.2

In [17]:
data

Rg_mean_y   T_mean_y  NEE_mean_y  VPD_mean_y   H_mean_y  LE_mean_y  \
0      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
1      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
2      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
3      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
4      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
5      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
6      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
7      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
8      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
9      136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
10     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
11     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
12     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
13     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
14     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
15     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
16     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
17     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
18     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
19     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
20     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
21     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
22     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
23     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
24     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
25     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
26     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
27     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
28     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
29     136.391922   6.803304    1.028648    3.243340   0.921629  35.689587   
...           ...        ...         ...         ...        ...        ...   
12516  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12517  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12518  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12519  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12520  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12521  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12522  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12523  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12524  199.526978  21.966225    0.049581   10.836235  55.573772  43.478092   
12525  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12526  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12527  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12528  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12529  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12530  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12531  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12532  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12533  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12534  101.492035  21.900930    0.503706   13.639494  47.221092  48.245052   
12535  101.492035  21.900930  

In [22]:
data.to_csv("../Data/df_val_q_t_y_m_%s_%s_%s_%s_%s_%s%s.csv" % (Dataset,extent,step,tau_max,min_len,alpha_level,attribute2))

In [23]:
data.drop( np.where(((data.DataPolicy=='Tier 1') | (data.DataPolicy=='Fair_Use'))==False)[0],inplace=True)

In [98]:
#data.drop(data[data.DataPolicy=='Tier 2'].index,inplace=True)
#data.drop(data[data.DataPolicy=='LaThuile_2007'].index,inplace=True)


In [25]:
data.to_csv("../Data/df_val_q_t_y_m_%s_%s_%s_%s_%s_%s%s_Tier1.csv" % (Dataset,extent,step,tau_max,min_len,alpha_level,attribute2))